Team Comparisons

In [1]:
import csv
import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression

Import Data

In [2]:
Stats = []
with open('TI9.csv', newline = '') as csvfile:
    spamreader = csv.reader(csvfile, delimiter = ',', quotechar='|')
    for row in spamreader:
        Stats.append(row)

Games Array

In [3]:
Team1 = []
Team2 = []
Winner = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        Team1.append(Stats[i][1])
        Team2.append(Stats[i][4])
        Winner.append(Stats[i][7])
        i += 1       

Total Wins per team

In [4]:
Teamlist = ['OG','Team Liquid', 'PSG.LGD','Team Secret','Vici Gaming','Evil Geniuses','Royal Never Give Up','Infamous Gaming', 'Newbee', 'TNC Predator','Virtus.pro','Fnatic','Alliance','Mineski','Natus Vincere', 'Chaos Esports Club', 'KEEN GAMING', 'Ninjas in Pyjamas']


wij = np.zeros((len(Teamlist), len(Teamlist)))


wincounts = []
for x in Teamlist:
    wincounts.append(Winner.count(x))

Wins i vs j matrix

In [5]:
binWins = np.zeros(len(Winner))
for i in range(len(Winner)):
    if Winner[i] == Team1[i]:
        binWins[i] = 1

d = {'Radiant':Team1, 'Dire':Team2, 'Winner':binWins}

index_dict = {'OG':0,'Team Liquid':1,'PSG.LGD':2,'Team Secret':3,'Vici Gaming':4,'Evil Geniuses':5,'Royal Never Give Up':6,'Infamous Gaming':7,'Newbee':8,'TNC Predator':9,'Virtus.pro':10,'Fnatic':11,'Alliance':12,'Mineski':13,'Natus Vincere':14,'Chaos Esports Club':15,'KEEN GAMING':16,'Ninjas in Pyjamas':17}

games = pd.DataFrame(data = d)

Wi = pd.DataFrame(np.array([wincounts]), columns = Teamlist)
    
np.array(wincounts)


for n in range(len(games.loc[:,'Radiant'])):
    i = games.loc[n,'Radiant']
    j = games.loc[n,'Dire']
    if games.loc[n,'Winner'] == i:
        wij[index_dict[i],index_dict[j]] += 1
    else:
        wij[index_dict[j],index_dict[i]] += 1

To implement the Bradley Terry Model as a GLM we will be relying on the logistic model for binomially distributed data as implemented by Jamil, 2010 such that logit(p_(i>j))= log(p_(i>j)/(1-p_(i>j)) = lamda_i - lambda_j


Model Matrix

From here we should be able to apply the logit model as we have pij, X and unknowns lambda where
logit[pij] = X*Lambda

Our inputs are clearly 2 teams with an output vector as 0 or 1 depending whether team 1 or team 2 wins

Lets do some quick Data fixing on our existing design and response matrixes

In [6]:
"""Number of teams"""
k = len(Teamlist)
N = len(Winner)
X = np.zeros((N,k))


def designMatrix(data, index_dict):
    """ Creates a design matrix for standard Bradley Terry Model"""
    N = len(data.index)
    k = len(index_dict.keys())
    X = np.zeros((N,k))
    gameNumber = 0
    for index, row in data.iterrows():
        X[gameNumber][index_dict[row[0]]] = 1
        X[gameNumber][index_dict[row[1]]] = -1
        gameNumber +=1
    return(X)

gameNumber = 0
for index, row in games.iterrows():
    X[gameNumber][index_dict[row['Radiant']]] = 1
    X[gameNumber][index_dict[row['Dire']]] = -1
    gameNumber+= 1
    
def BTfit(X, Y, Teamlist, tol):
    N = len(Y)
    k = len(Teamlist)
    X = np.matrix(X)
    Xt = np.matrix.transpose(X)
    XXt = np.dot(X,Xt)
    Y = np.matrix(Y)
    Y = np.matrix.transpose(Y)
    rankings = np.matrix(np.random.rand(k,1))
    tol = 1
    t = 0
    while tol > 0.00001:
        p = np.exp(np.dot(X,rankings))/(1+np.exp(np.dot(X,rankings)))
        gradient = np.matrix(np.zeros((1,k)))
        hessian = 0
        for i in range(N):
            gradient += np.multiply(X[i],Y[i]) - np.multiply(X[i],p[i])
            hessian += XXt.item((i,i))*p[i]*(1-p[i])
    
        
        oldrankings = np.matrix.transpose(rankings)
        rankings = oldrankings + (1/hessian)*gradient
    
        tol = np.dot(rankings-oldrankings, np.matrix.transpose(rankings-oldrankings))
        rankings = np.matrix.transpose(rankings)
    rankings = np.exp(rankings)   
    ranks = np.asarray(rankings)
    ranks = np.ndarray.tolist(ranks)
    data = {"Teams":Teamlist, "Ranks":ranks}
    Teamskills = pd.DataFrame(data)
    return(Teamskills)
    
test = designMatrix(games, index_dict)
test2 = BTfit(test, binWins, Teamlist,1)
print(test2)
    
X = np.matrix(X)
Xt = np.matrix.transpose(X)
XXt = np.dot(X,Xt)
Y = np.matrix(binWins)
Y = np.matrix.transpose(Y)
rankings = np.matrix(np.random.rand(k,1))
tol = 1.


Exception: Data must be 1-dimensional

In [7]:
while tol > 0.00001:
    p = np.exp(np.dot(X,rankings))/(1+np.exp(np.dot(X,rankings)))
    gradient = np.matrix(np.zeros((1,k)))
    hessian = 0
    for i in range(N):
        gradient += np.multiply(X[i],Y[i]) - np.multiply(X[i],p[i])
        hessian += XXt.item((i,i))*p[i]*(1-p[i])
        
    oldrankings = np.matrix.transpose(rankings)
    rankings = oldrankings + (1/hessian)*gradient
    
    tol = np.dot(rankings-oldrankings, np.matrix.transpose(rankings-oldrankings))
    rankings = np.matrix.transpose(rankings)

Hero Ratings

In [8]:
heroes1 = []
heroes2 = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        heroes1.append(Stats[i][2])
        heroes2.append(Stats[i][5])
        i += 1   

In [9]:
heroes1

['Io  Tiny  Abaddon  Timbersaw  Gyrocopter',
 'Rubick  Tidehunter  Ogre Magi  Templar Assassin  Juggernaut',
 'Tidehunter  Templar Assassin  Shadow Shaman  Lifestealer  Enigma',
 'Tidehunter  Chen  Rubick  Templar Assassin  Meepo',
 'Elder Titan  Rubick  Faceless Void  Shadow Fiend  Dark Seer',
 'Elder Titan  Rubick  Sven  Dark Seer  Templar Assassin',
 'Tiny  Faceless Void  Mirana  Tinker  Shadow Demon',
 'Elder Titan  Rubick  Magnus  Wraith King  Bristleback',
 'Chen  Tidehunter  Earth Spirit  Leshrac  Meepo',
 'Chen  Alchemist  Tidehunter  Rubick  Legion Commander',
 'Shadow Demon  Sand King  Jakiro  Sven  Dragon Knight',
 "Elder Titan  Faceless Void  Pangolier  Nature's Prophet  Zeus",
 'Tiny  Omniknight  Windranger  Crystal Maiden  Bristleback',
 'Leshrac  Tidehunter  Lion  Earth Spirit  Medusa',
 'Elder Titan  Alchemist  Rubick  Ember Spirit  Dark Seer',
 'Mirana  Ogre Magi  Tidehunter  Faceless Void  Tinker',
 'Tiny  Faceless Void  Witch Doctor  Enigma  Abaddon',
 'Magnus  Shado

Firstly we need to count comparative wins separately, then we will compare them as a team

In [10]:
heroes1new = []
heroes2new = []
for i in heroes1:
    heroes1new.append(i.split("  "))

for i in heroes2:
    heroes2new.append(i.split("  "))

In [11]:
#Herodict goes here
l = 0
hdict = {}
for i in heroes1new:
    for j in i:
        if j in hdict:
            continue
        else:
            hdict[j] = l
            l += 1

for i in heroes2new:
    for j in i:
        if j in hdict:
            continue
        else:
            hdict[j] = l
            l += 1
hdict

{'Io': 0,
 'Tiny': 1,
 'Abaddon': 2,
 'Timbersaw': 3,
 'Gyrocopter': 4,
 'Rubick': 5,
 'Tidehunter': 6,
 'Ogre Magi': 7,
 'Templar Assassin': 8,
 'Juggernaut': 9,
 'Shadow Shaman': 10,
 'Lifestealer': 11,
 'Enigma': 12,
 'Chen': 13,
 'Meepo': 14,
 'Elder Titan': 15,
 'Faceless Void': 16,
 'Shadow Fiend': 17,
 'Dark Seer': 18,
 'Sven': 19,
 'Mirana': 20,
 'Tinker': 21,
 'Shadow Demon': 22,
 'Magnus': 23,
 'Wraith King': 24,
 'Bristleback': 25,
 'Earth Spirit': 26,
 'Leshrac': 27,
 'Alchemist': 28,
 'Legion Commander': 29,
 'Sand King': 30,
 'Jakiro': 31,
 'Dragon Knight': 32,
 'Pangolier': 33,
 "Nature's Prophet": 34,
 'Zeus': 35,
 'Omniknight': 36,
 'Windranger': 37,
 'Crystal Maiden': 38,
 'Lion': 39,
 'Medusa': 40,
 'Ember Spirit': 41,
 'Witch Doctor': 42,
 'Silencer': 43,
 'Phantom Lancer': 44,
 'Riki': 45,
 'Ancient Apparition': 46,
 'Arc Warden': 47,
 'Centaur Warrunner': 48,
 'Enchantress': 49,
 'Invoker': 50,
 'Earthshaker': 51,
 'Oracle': 52,
 'Terrorblade': 53,
 'Lina': 54,
 '

Now to try and break down all possible matchups (which is a fuckload)

In [12]:
Matchups1 = []
binWins2 = []
for i in heroes1new:
    for j in i:
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)


Matchups2 = []
for i in heroes2new:
    for j in range(5):
        Matchups2.append(i[0])
        Matchups2.append(i[1])
        Matchups2.append(i[2])
        Matchups2.append(i[3])
        Matchups2.append(i[4])

    
for i in binWins:
    for j in range(25):
        binWins2.append(i)

d = {'Radiant':Matchups1, 'Dire':Matchups2, 'Winner':binWins2}
heroGames = pd.DataFrame(data = d)


In [13]:
"""Number of Heroes"""
k = len(hdict.keys())
""" Number of Comparisons """
N = len(binWins2)
""" Design Matrix """
X = np.zeros((N,k))
gameNumber = 0
for index, row in heroGames.iterrows():
    X[gameNumber][hdict[row['Radiant']]] = 1
    X[gameNumber][hdict[row['Dire']]] = -1
    gameNumber+= 1
test3 = designMatrix(heroGames, hdict)    

X = np.matrix(X)
Xt = np.matrix.transpose(X)
XXt = np.dot(X,Xt)
Y = np.matrix(binWins2)
Y = np.matrix.transpose(Y)
rankings = np.matrix(np.random.rand(k,1))
tol = 1.


In [14]:
ranks = np.asarray(rankings)
ranks = np.ndarray.tolist(ranks)

heroes = []
for i in hdict.keys():
    heroes.append(i)
    
data = {"Heroes":heroes, "Ranks":ranks}
data
Heroskills = pd.DataFrame(data)
Heroskills

test4 = BTfit(test3, binWins2, heroes,1)

Lets do some data fixing now on rankings and our two data frames

In [15]:
Heroskills = Heroskills.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [16]:
heroes = []
for i in hdict.keys():
    heroes.append(i)

How do we interpret the 2 ratings, for teams it is clear, but for heroes i imagine we can add up the skills of both teams and treat them as a single team, to test

for treating heroes as players in a team we refer back to Haziq

We shall first implement this for team OG, haziq does this for liverpool and we will implement this in a similar way, what is worth noting for the final potential model is that in the EPL model there are no shared players while in ours "players" will predominantly be shared

From Huang et al. 2006

In [17]:
""" Consider k individuals """
k = len(hdict.keys())
k

115

In [18]:
for i in heroes1new:
    i.sort()

In [19]:
I = []
for i in heroes1new:
    l = 0
    for j in heroes1new:
        if l == 0:
            continue
        elif i == j:
            print(True)
        l+=1
    for j in heroes2new:
        if i ==j:
            print(True)

In [20]:
ri = binWins
herodf = pd.DataFrame(data = {"Radiant": heroes1new, "Dire": heroes2new, "Winner":binWins})

In [21]:
q = np.zeros(len(hdict.keys()))
qplus = np.zeros(len(hdict.keys()))
qminus = np.zeros(len(hdict.keys()))
game = 0
for hero in hdict.keys():
    for i in range(len(binWins)):
        if hero in herodf["Radiant"][i]:
            if herodf["Winner"][i] == 1:
                q[hdict[hero]] += 1
                qplus[hdict[hero]] += 1
        elif hero in herodf["Dire"][i]:
            if herodf["Winner"][i] == 0:
                q[hdict[hero]] += 1
                qminus[hdict[hero]] += 1
        else:
            continue

In [22]:
qminus

array([ 9., 15.,  4.,  2., 15., 12., 16., 13.,  6.,  2.,  4., 13.,  6.,
        8.,  1., 27.,  9.,  2.,  2., 10., 14.,  1., 25.,  5.,  7.,  4.,
        4., 13.,  7.,  3., 13.,  4.,  4.,  4.,  1.,  0.,  5.,  7., 10.,
        7.,  3.,  9.,  4.,  0.,  1.,  0.,  7.,  2., 10., 11.,  7., 11.,
        3.,  1.,  7.,  1.,  5.,  2., 14.,  4.,  0.,  4.,  0.,  0.,  4.,
        8.,  2.,  2.,  5.,  8.,  1.,  4.,  2.,  3.,  2.,  2.,  1.,  1.,
        4.,  1.,  1.,  8.,  2.,  0.,  3.,  0.,  2.,  4.,  4.,  0.,  4.,
        0.,  0.,  0.,  0.,  1.,  1.,  2.,  0.,  3.,  0.,  0.,  6.,  0.,
        0.,  1.,  5.,  0.,  1.,  0.,  1.,  1.,  0.,  0.,  0.])

In [23]:
k = len(hdict.keys())
m = len(binWins)
Ip = np.zeros((m,k))
I = np.zeros((m,k))
l = 0
r = binWins
for i in heroes1new:
    for j in i:
        if binWins[l] == 1:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
        l+=1
        
    l = 0
for i in heroes2new:
    for j in i:
        if binWins[l] == 0:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l += 1
    
po = np.ones(k)/k
maxiter = 1000;
delta = np.zeros(k)

def newI(team1,team2, k, m, index_dict):
    I = np.zeros((m,k))
    l = 0
    
    for i in team1:
        for j in i:
            I[l,index_dict[j]] = 1
        l += 1
    l = 0
    for i in team2:
        for j in i:
            I[l,index_dict[j]] = 1
        l += 1
    return(I)

def newIp(team1, k, m, index_dict):
    Ip =np.zeros((m,k))
    l = 0
    for i in team1:
        for j in i:
            Ip[l,index_dict[j]] = 1
        l+=1
    return(Ip)

def BTfit2(I,Ip,r,k,maxiter,playerlist):
    po = np.random.rand(k)
    delta = np.zeros(k)
    for t in range(maxiter):
        for i in range(k):
            pp = np.tile(np.transpose(po), (r.size,1))
            qp = np.sum(np.multiply(pp,Ip),axis=1)
            Ipp = Ip[:,i]
            q = np.sum(np.multiply(pp,I),axis=1)
            Ii = I[:,i]
            Ipp = Ipp.astype(int)
            Ii = Ii.astype(int)
            delta[i] = np.sum(np.divide(r[Ipp],qp[Ipp]))/np.sum(np.divide(r[Ii],q[Ii]))
            if np.isnan(delta[i]):
                print(po)
                print(delta)
                print(qp[Ipp])
                print(q[Ii])
                break
            po[i] = delta[i]*po[i]
            po = po/np.sum(po)
        if np.max(np.abs(delta-1)) < 0.001:
            separate = t*k
            break
    pest = po
    data = {"Heroes":playerlist, "Ranks":pest}
    Heroskills2 = pd.DataFrame(data)
    return(Heroskills2)
    
    
    
    
for t in range(maxiter):
    for i in range(k):
        pp = np.tile(np.transpose(po), (binWins.size,1))
        qp = np.sum(np.multiply(pp,Ip),axis=1)
        Ipp = Ip[:,i]
        q = np.sum(np.multiply(pp,I),axis=1)
        Ii = I[:,i]
        Ipp = Ipp.astype(int)
        Ii = Ii.astype(int)
        delta[i] = np.sum(np.divide(r[Ipp],qp[Ipp]))/np.sum(np.divide(r[Ii],q[Ii]))
        if np.isnan(delta[i]):
            print(po)
            print(delta)
            print(qp[Ipp])
            print(q[Ii])
            break
        po[i] = delta[i]*po[i]
        po = po/np.sum(po)
    if np.max(np.abs(delta-1)) < 0.001:
        separate = t*k
        break
pest = po                        
        
        
test5 = BTfit2(I,Ip,binWins,k,10,heroes)
test5


Heroes     Ranks
0                Io  0.002418
1              Tiny  0.020281
2           Abaddon  0.017755
3         Timbersaw  0.005078
4        Gyrocopter  0.012731
..              ...       ...
110  Spirit Breaker  0.002767
111   Night Stalker  0.003425
112   Bounty Hunter  0.012304
113      Venomancer  0.001251
114    Ember Spirit  0.006656

[115 rows x 2 columns]

Start with initial p_j^0 > 0, j = 1,...,k and obtain corresponding qi's values for i = 1,...,m
k = no.heros
m = no.games



In [24]:
pest/np.min(pest)

array([4.15664897e+09, 1.41287231e+33, 5.33880590e+11, 3.99665343e+11,
       4.88251635e+30, 1.96090336e+22, 1.65747722e+20, 2.96461388e+51,
       1.19650899e+07, 2.54963297e+16, 5.26780997e+11, 2.95649552e+51,
       1.63430311e+19, 9.51048945e+11, 2.01538297e+02, 2.54002755e+41,
       1.25849115e+12, 1.74403607e+09, 1.96198420e+02, 1.06117961e+22,
       1.80841981e+25, 3.71407042e+04, 2.30092479e+58, 1.23375512e+19,
       1.14492409e+07, 9.61707643e+06, 5.84230717e+11, 3.88779057e+43,
       7.62887277e+11, 8.28408963e+13, 8.88777828e+24, 3.56096971e+16,
       4.22955878e+04, 2.88548941e+16, 7.18560061e+06, 3.19806179e+04,
       1.39308225e+14, 1.28617477e+07, 1.12159925e+22, 3.28002371e+09,
       4.38726091e+04, 8.39145507e+21, 2.30155883e+09, 6.46071095e+13,
       1.46344116e+09, 1.89703843e+02, 4.79795770e+21, 2.05132107e+02,
       3.65391315e+24, 5.50679359e+14, 9.58072809e+11, 1.75960621e+27,
       2.00996632e+09, 7.73804043e+06, 1.40214435e+24, 7.73804043e+06,
      

In [25]:
data = {"Heroes":heroes, "Ranks":pest}
data
Heroskills2 =test5
Heroskills2

Heroes     Ranks
0                Io  0.002418
1              Tiny  0.020281
2           Abaddon  0.017755
3         Timbersaw  0.005078
4        Gyrocopter  0.012731
..              ...       ...
110  Spirit Breaker  0.002767
111   Night Stalker  0.003425
112   Bounty Hunter  0.012304
113      Venomancer  0.001251
114    Ember Spirit  0.006656

[115 rows x 2 columns]

Compare these results to overall pick rate, and how it changes over time as the model begins to converge

Cool, so we've implemented two models for hero weighting, likely should implement the combined model now, additionally should place these into functions so that we can develop train/test data for analytics

Combined Model: The idea behind the comparative model is to treat the heroes picked in the game as a homeground advantage by seeing which composition has the highest win-probability according to previous model (sum of player skills is the teams skill independent of which team is playing) additionally there is likely ways to treat it as a second logistic parameter but ya boi dumb so...

Imma do this with directly optimizing the log likelihood cause i a lazy bitch

In [26]:
"aij be the number of times i beats j at home"
k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(binWins)

def BTloglik(li):
    lilj = np.zeros(len(li[:-1]))
    for i in range(len(li[:-1])):
        for j in range(len(li[:-1])):
            if i != j:
                lilj[i] += (li[-1]*li[i]+li[j])
    print(lilj)
    ll = c*np.log(li[-1]) + np.sum(np.multiply(wincounts,np.log(li[:-1])))-np.sum(np.dot(nij,np.log(lilj)))
    return(-ll)

x0 = np.random.rand(k+1)
len(x0[:-1])
wincounts
#np.multiply(Wi,x0[:-2])
BTloglik(x0)


[15.85489353 10.15723329 22.41986365  8.67028963 15.42633714 12.1498202
  9.97137298 22.94168417 14.28351803 13.42527125 10.00287502 19.95400155
 10.16363691 10.26970664 10.16913007 18.34914394 16.87996086 10.5786385 ]


726.7459429511451

In [27]:
from scipy.optimize import minimize

In [28]:
np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

[35.49068274 17.93216801 14.28898736 15.11007733 21.99042474 18.42404661
 28.05079017 20.46713302 24.3864876  17.32380084 26.06708792 25.00471764
  9.56890075 11.712105   15.75069791 12.36810418 23.49490328 16.47992257]
[34.10626899 17.62337738 14.28226578 14.62110718 21.77209647 18.81296132
 27.80179601 20.6149035  24.18979086 17.66925549 25.96821147 24.99309397
  9.6341365  11.73620729 15.68778939 12.70298504 23.20476649 17.48006401]
[37.84381656 18.35809655 14.42415751 15.59159131 22.34562355 17.82939228
 28.99262944 20.04018293 24.58770752 16.52160947 26.94729031 24.61945637
  9.42343354 11.63294533 15.8959558  10.3308063  23.76372043 14.36334281]
[39.06808458 18.6645381  14.65703879 15.74168634 22.55181992 17.54360546
 28.0279041  20.01866665 24.87592378 15.84971708 28.23813265 24.95325976
  9.30714123 11.54940232 15.99692671  9.13461427 23.44742836 12.8328851 ]
[35.62276848 17.89505865 14.26415913 15.08386183 21.99791755 18.39997791
 28.83972665 20.31441527 24.28738004 17.3256718

c:\users\rowan\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log


[34.85053283 17.81343893 14.07651542 15.10161525 20.86419715 15.45345276
 28.46490359 18.98903957 21.06684688 15.77729284 26.57057016 19.73639032
  8.99752448 11.17901176 15.8946975  12.87491685 20.78081608 11.40082108]
[35.79381719 18.00151635 14.2055294  15.17772174 20.83669898 16.1335933
 27.97443059 19.63907954 21.85997268 16.44653293 26.32330666 21.42803508
  9.15564513 11.24527443 15.83938335 12.31820343 22.14869444 12.27471426]
[35.78066491 18.23701421 14.44491205 15.28461501 21.0766028  15.20472427
 28.92995061 18.3757971  20.87039881 15.39807146 26.84294776 20.27398255
  8.90918758 11.11474251 15.97499892 12.15293338 21.45896559 10.22674344]
[35.95837221 18.07443214 14.35887924 15.258996   21.70036698 16.59809984
 28.43956954 19.07229711 21.48331491 16.06333984 26.62918124 21.37214438
  9.10192612 11.26282713 15.64983214 12.14696479 22.06778797 11.96616764]
[34.34022545 17.82927595 14.17034282 15.04459482 20.76591263 16.01168258
 27.99171988 18.76757345 21.02482547 16.03346179

[21.22646336 15.59321269 13.90288798 14.92649895 17.99913757 14.1332723
 30.16365718 15.82541628 17.3830441  14.85369475 21.25149786 15.90969199
  8.26919332 10.4245588  13.90666374 11.34394742 15.71390728  9.84543532]
[22.13021162 15.50428807 13.75033178 14.90739212 17.81195933 14.37018433
 29.8936766  15.37258831 17.33396482 14.56350956 20.7982159  16.98281604
  8.28735375 10.50125936 13.79349776 10.39363808 15.57107494  9.5462209 ]
[21.11340276 14.98584028 13.45342492 14.63042121 16.86271529 14.25389604
 29.15201326 14.3829946  16.23798824 14.55435125 19.523853   17.04688402
  8.19136378 10.33269703 13.35513385 10.03261412 14.50886492  9.09080996]
[21.71886928 15.4906403  13.74298016 14.72304866 17.62292275 14.97497969
 29.50907021 15.1648422  17.23343538 14.96592058 20.43522285 18.1064572
  8.36261108 10.53680262 13.7249568  10.83421045 15.75173711 10.1819741 ]
[21.25192344 15.38733599 13.61426822 14.55163848 17.44356786 14.63409681
 29.23754383 14.53794785 17.10698962 14.8888128  

...

[9.59246928 9.02587802 7.42034988 8.31009753 7.76755293 6.78577027
 6.80986274 5.98799161 6.88854261 6.5342531  5.58287444 6.15797729
 4.10690551 7.22260121 9.25340595 4.69269114 5.73479039 4.64434742]
[9.66612708 9.13462954 7.44029938 8.39162102 7.84295793 7.09530975
 6.92792976 5.97511394 6.94396462 6.53937231 5.74532027 6.29217016
 4.1298062  7.25769604 9.30848246 4.72306818 5.73382805 4.63725771]
[9.44542566 8.80642975 7.27087276 8.24516912 7.63252871 6.48550762
 6.46443276 5.95902702 6.79841314 6.55664697 5.46953052 5.95803563
 4.0538247  7.27652153 9.29316694 4.40368711 5.83320227 4.6860766 ]
[9.38353082 8.76685057 7.23657969 8.43306591 7.68792167 6.51669384
 6.74861107 5.9053593  7.03716527 6.6292609  5.34843659 5.96182449
 4.03796118 7.38287826 9.22698034 4.61574057 5.89512999 4.43114436]
[9.56427023 8.9677097  7.44775315 8.15069238 7.6888384  6.48701648
 6.64673274 6.03094089 6.74800738 6.49012542 5.46987636 6.05058365
 4.10132133 7.11997841 9.19837438 4.64952464 5.68246475 4.

[9.44364057 8.82805794 7.26051495 8.25762447 7.74697902 6.52485772
 6.79320062 5.90450356 6.94095853 6.25623663 5.34227338 6.09965817
 4.05494706 7.26614687 9.01940815 4.54899651 5.6516051  4.66267037]
[9.64823573 8.81854691 7.19868232 8.12765878 7.84882904 6.52910725
 6.69919681 5.89762057 6.91665503 6.22074128 5.33528976 6.10663677
 4.06497366 7.24973502 8.925325   4.51346624 5.58254549 4.63444029]
[9.75651144 8.96410911 7.3571708  8.20407512 7.85168621 6.64741461
 6.71560832 5.9548678  6.83382616 6.29697128 5.4147519  6.24344547
 4.08788825 7.24356142 9.05968733 4.53043305 5.64700641 4.7675754 ]
[9.7305521  8.9606295  7.36139286 8.26098343 7.81637588 6.6066754
 6.78734912 5.87612742 6.93274941 6.29839869 5.48499646 6.26630991
 4.09009438 7.26527362 9.10583494 4.53031766 5.74741585 4.70334164]
[9.45710777 8.79853394 7.23218069 8.08771597 7.7795715  6.53699964
 6.55589557 5.82853956 6.7693507  6.23838852 5.30644329 5.90006247
 4.04400415 7.18753829 8.88748874 4.50110059 5.57884625 4.6

[9.65593745 8.95362048 7.33325075 8.27324564 8.06088149 6.68598008
 6.8166929  5.8158158  7.20848976 6.37255011 5.39374333 6.19076419
 4.08433337 7.33697308 9.01548704 4.55726846 5.65251228 4.72756188]
[9.61945555 8.90180329 7.29807119 8.21801963 7.97141575 6.60192794
 6.757958   5.8246531  7.11707899 6.36261445 5.36992783 6.186609
 4.08134981 7.30018316 9.00158686 4.55428749 5.66316888 4.74105891]
[9.56553175 8.85721053 7.24853903 8.174396   7.93487657 6.51943229
 6.68251818 5.82161934 7.10666137 6.3391022  5.36086815 6.15466856
 4.07383516 7.28919227 9.00316283 4.53318627 5.66720698 4.75890137]
[9.70482824 8.95120193 7.34233291 8.29017793 8.06519759 6.68631083
 6.89452186 5.83081783 7.17518123 6.3347241  5.38661085 6.23002259
 4.08726936 7.3454482  8.9635635  4.54662954 5.68847314 4.67905039]
[9.69977228 8.93200364 7.33032422 8.24284701 8.03782783 6.62603572
 6.86094365 5.78756819 7.09880618 6.39560038 5.34281115 6.24742963
 4.0830342  7.32748573 8.97737228 4.58843689 5.61329897 4.70

[9.54645257 8.89545366 7.27744475 8.20692158 8.02362625 6.62310549
 6.76504506 5.76444181 7.08156638 6.3637955  5.33397553 6.16529838
 4.06825156 7.31271565 8.94892915 4.56594421 5.6167214  4.69962125]
[9.61491447 8.93401247 7.31756599 8.28566124 8.06826175 6.66695633
 6.87998467 5.87659327 7.15537956 6.37713329 5.38535244 6.29717216
 4.0873861  7.36417462 8.9969864  4.56423459 5.69896836 4.7447081 ]
[9.58835592 8.89818454 7.30543867 8.28768284 8.02179933 6.67909199
 6.86738404 5.78201673 7.10189437 6.35022375 5.34438782 6.22372841
 4.07187629 7.35318497 8.93861089 4.51876604 5.68866252 4.68664253]
[9.6948347  9.00080024 7.38685511 8.25527427 8.11362398 6.68362396
 6.83239898 5.85456186 7.20080253 6.4137205  5.40195053 6.26841226
 4.10063383 7.32409081 9.01323814 4.58528558 5.68100133 4.7686665 ]
[9.71166487 9.0058314  7.40872412 8.24329911 8.10236734 6.69878944
 6.80334756 5.78234321 7.18495793 6.41167415 5.38197873 6.20725457
 4.09611433 7.29933666 8.98144895 4.56429237 5.66634425 4.

[9.81627092 9.04788393 7.45926348 8.28604862 8.18987677 6.62084054
 6.90669099 5.84310818 7.19011583 6.42741424 5.39782164 6.29411958
 4.10328875 7.34717011 9.00398659 4.56181135 5.69996565 4.74594378]
[9.89092844 9.08512606 7.51154895 8.31207563 8.20434205 6.62814837
 6.93532413 5.8564923  7.15353125 6.42291976 5.41176523 6.29153681
 4.10604909 7.34895504 9.00787386 4.55275637 5.72665854 4.72535702]
[9.73371537 9.03519493 7.42765169 8.24161991 8.10476685 6.54535124
 6.82597018 5.85043182 7.22623339 6.40454105 5.41643299 6.27090807
 4.10160196 7.30026016 9.07379916 4.5787395  5.65986643 4.78042498]
[9.7820692  9.00376665 7.41914346 8.24143231 8.17055564 6.57217665
 6.86664172 5.80685087 7.14044296 6.47045962 5.35903404 6.34001369
 4.10115347 7.34415427 8.97873653 4.56800022 5.70776154 4.76363391]
[9.73367464 8.92849061 7.37409211 8.2543138  8.10049551 6.57245092
 6.89918224 5.87205273 7.21001221 6.43294171 5.3622104  6.24498036
 4.10234232 7.33751563 8.96288659 4.54960257 5.68691516 4.

In [29]:
data = {"Teams":Teamlist, "Ranks":res.x[:-1]/np.min(res.x[:-1]),"Radiant Advantage":res.x[-1]}
data
Teamhg = pd.DataFrame(data)
Teamhg.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg

Teams      Ranks  Radiant Advantage
0                    OG  18.053787           0.915161
1           Team Liquid  15.822115           0.915161
14        Natus Vincere  15.641570           0.915161
3           Team Secret  13.610140           0.915161
4           Vici Gaming  13.523732           0.915161
2               PSG.LGD  11.035274           0.915161
13              Mineski  10.865921           0.915161
8                Newbee  10.634655           0.915161
6   Royal Never Give Up   9.441427           0.915161
5         Evil Geniuses   8.551742           0.915161
9          TNC Predator   8.062199           0.915161
11               Fnatic   7.491167           0.915161
7       Infamous Gaming   6.233234           0.915161
16          KEEN GAMING   5.833543           0.915161
10           Virtus.pro   4.816592           0.915161
17    Ninjas in Pyjamas   3.058589           0.915161
15   Chaos Esports Club   2.348975           0.915161
12             Alliance   1.000000           0.915161

In [30]:
np.sum(aij,axis=1)

array([ 8., 13.,  3.,  8.,  7.,  4.,  5.,  2.,  7.,  5.,  2.,  5.,  4.,
        5.,  5.,  1.,  3.,  2.])

In [31]:
Teamlist

['OG',
 'Team Liquid',
 'PSG.LGD',
 'Team Secret',
 'Vici Gaming',
 'Evil Geniuses',
 'Royal Never Give Up',
 'Infamous Gaming',
 'Newbee',
 'TNC Predator',
 'Virtus.pro',
 'Fnatic',
 'Alliance',
 'Mineski',
 'Natus Vincere',
 'Chaos Esports Club',
 'KEEN GAMING',
 'Ninjas in Pyjamas']

In [32]:
np.sum(bij,axis=1)

array([1., 9., 3., 6., 5., 2., 8., 5., 7., 8., 7., 8., 3., 5., 5., 5., 8.,
       9.])

Lets add some extra data to represent whether a team's composition has won

In [33]:
Teamskill1 = np.zeros(m)
Teamskill2 = np.zeros(m)

index = 0
for i in heroes1new:
    for j in i:
        Teamskill1[index] += test4["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in heroes2new:
    for j in i:
        Teamskill2[index] += test4["Ranks"][hdict[j]][0]
    index += 1

In [34]:
Teamwin1 = np.zeros(m)
for i in range(m):
    prob = Teamskill1[i]/(Teamskill1[i]+Teamskill2[i])
    if prob >= 0.5:
        Teamwin1[i] = 1

In [35]:
Teamwin1

array([1., 1., 1., 1., 0., 1., 1., 0., 1., 1., 0., 0., 1., 0., 1., 1., 1.,
       0., 1., 0., 0., 1., 1., 0., 1., 0., 1., 0., 1., 0., 0., 0., 0., 1.,
       1., 0., 1., 0., 1., 0., 0., 0., 1., 0., 0., 0., 1., 0., 1., 1., 1.,
       1., 0., 0., 0., 1., 1., 0., 0., 1., 0., 0., 0., 1., 0., 1., 1., 0.,
       1., 0., 0., 0., 0., 0., 1., 0., 1., 0., 0., 1., 0., 0., 0., 1., 0.,
       0., 0., 1., 1., 0., 1., 0., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0.,
       0., 1., 0., 0., 1., 1., 0., 1., 1., 1., 0., 1., 0., 1., 1., 0., 0.,
       0., 0., 0., 0., 1., 1., 0., 0., 1., 1., 1., 0., 1., 0., 1., 0., 0.,
       0., 1., 1., 0., 0., 1., 1., 1., 0., 0., 1., 0., 0., 1., 1., 1., 1.,
       1., 1., 0., 1., 0., 0., 0., 1., 1., 0., 1., 1., 0., 0., 1., 0., 0.,
       0., 1., 1., 0., 1., 1., 0., 1., 0., 1., 0., 0., 1., 0., 1., 0., 1.,
       1., 0., 1., 0., 1., 1.])

In [36]:
games['Team Winner'] = Teamwin1

In [37]:
Teamskill3 = np.zeros(m)
Teamskill4 = np.zeros(m)

index = 0
m = len(games["Winner"])
for i in heroes1new:
    for j in i:
            Teamskill3[index] += Heroskills2["Ranks"][hdict[j]]
    index += 1

index = 0
for i in heroes2new:
    for j in i:
            Teamskill4[index] += Heroskills2["Ranks"][hdict[j]]            
    index += 1

Teamskill3

array([0.05826342, 0.04932284, 0.03253164, 0.05574972, 0.04887126,
       0.05352506, 0.04309852, 0.06411888, 0.03571842, 0.06776762,
       0.05639122, 0.04201568, 0.06271853, 0.03704253, 0.07154188,
       0.03481156, 0.04904427, 0.03908353, 0.05278815, 0.06011708,
       0.04127911, 0.06949787, 0.03508317, 0.04226109, 0.05031455,
       0.04408484, 0.03542285, 0.0371827 , 0.05242269, 0.0518443 ,
       0.04519477, 0.03936148, 0.04551651, 0.03469151, 0.05307554,
       0.03481139, 0.06333757, 0.08143103, 0.08286964, 0.06102032,
       0.05395104, 0.04912828, 0.03968447, 0.05847694, 0.07712766,
       0.06134621, 0.02937076, 0.05971084, 0.07129871, 0.04490069,
       0.08045464, 0.06307551, 0.03238673, 0.03857766, 0.0312012 ,
       0.06567071, 0.0638584 , 0.02446147, 0.04537502, 0.06099109,
       0.05256598, 0.06051679, 0.05389125, 0.06251273, 0.0502998 ,
       0.05499471, 0.0405897 , 0.02522729, 0.04869808, 0.03803977,
       0.06148235, 0.05109231, 0.05530843, 0.05517525, 0.06220

In [38]:
Teamwin2 = np.zeros(m)
for i in range(m):
    if Teamskill3[i] > Teamskill4[i]:
        Teamwin2[i] = 1

Teamwin2

array([1., 0., 0., 1., 1., 0., 0., 1., 0., 1., 0., 0., 0., 0., 1., 0., 1.,
       0., 1., 1., 0., 1., 0., 0., 0., 0., 0., 0., 1., 1., 1., 0., 0., 0.,
       1., 0., 1., 1., 1., 1., 1., 1., 0., 1., 1., 0., 1., 1., 1., 0., 1.,
       1., 0., 0., 0., 1., 0., 0., 1., 1., 1., 0., 1., 1., 0., 0., 1., 0.,
       1., 0., 1., 1., 0., 1., 1., 1., 1., 1., 0., 0., 0., 1., 1., 0., 1.,
       1., 0., 1., 1., 1., 1., 1., 1., 0., 0., 0., 1., 0., 1., 0., 0., 0.,
       0., 0., 1., 1., 0., 1., 0., 0., 1., 1., 1., 0., 1., 1., 0., 1., 0.,
       0., 0., 0., 0., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0., 1., 0., 1.,
       1., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0., 1., 0.,
       1., 1., 1., 1., 0., 0., 0., 1., 1., 0., 0., 1., 0., 0., 0., 1., 1.,
       1., 0., 1., 0., 1., 0., 0., 0., 0., 1., 0., 0., 1., 0., 0., 0., 0.,
       1., 1., 0., 1., 0., 0.])

In [39]:
games['Team Winner 2'] = Teamwin2

In [40]:
k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Team Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(games["Team Winner"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 1":np.exp(res.x[-1])}

Teamhg2 = pd.DataFrame(data)
Teamhg2.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg2

k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Team Winner 2"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(games["Team Winner 2"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 2":np.exp(res.x[-1])}

Teamhg3 = pd.DataFrame(data)
Teamhg3.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg3


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

[27.98271537 17.39476715 13.82431285 13.84255313 20.59559566 19.72310829
 26.27619649 22.45453596 22.61803317 17.40211452 22.66564522 27.31642643
  9.86753027 11.86337713 15.84357463 13.24066188 20.57378394 26.87379108]
[28.5850496  17.89793273 13.9582757  13.85278751 20.90282762 19.77672243
 26.31708005 22.07204033 22.73222664 16.56940324 22.68852783 27.73211
  9.75659121 11.82855931 16.0652769  11.82531862 19.81812702 27.59273782]
[28.20313673 17.66013487 13.93682524 13.94692142 20.25597679 19.69912982
 26.61368812 23.42174604 22.65156859 17.54738221 22.94582854 27.79913337
  9.84414338 11.8920552  15.94210353 13.11759591 20.59784827 27.14670881]
[27.32839805 17.34229805 13.79512086 13.810377   20.05924288 19.19502467
 25.67749433 22.77449638 22.01223045 17.20582139 22.25066577 26.93539268
  9.83676017 11.78102257 15.67120351 12.80705427 19.8696718  26.11770398]
[27.9053163  17.62410187 13.89666996 13.83996488 20.72739075 19.35134128
 26.3269048  23.5344417  22.25710157 17.10936247 2

c:\users\rowan\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log



[27.99978527 21.48825459 14.96139765 14.21257449 21.71454067 14.51994391
 25.29533742 23.84199655 16.65095176 14.65533003 22.0305027  38.52470458
  9.02822266 11.87138176 16.93860568 10.36249008 18.83839542 19.62504804]
[27.96006584 21.40358219 14.94591178 14.16345682 21.78127925 14.12015078
 25.13354119 23.83524522 16.80516846 14.43347467 21.80179693 38.63004679
  9.0448825  11.84715649 16.72684238 10.70296593 19.1398645  19.37594478]
[28.02124838 21.68012017 14.90097459 14.19625851 21.60935452 14.28019693
 24.76240592 23.80809026 16.78979634 13.84440004 21.92537371 38.31401488
  8.97937811 11.81728129 17.06256414 10.02543746 18.99724494 19.21442038]
[27.77501854 21.61808785 14.93843085 14.1253956  21.86321065 14.04754349
 24.62552275 23.68624157 16.06188697 14.22197054 21.39299594 39.62399757
  8.99630788 11.86919658 16.84675568 10.54547328 18.91726062 19.0738958 ]
[28.45506019 22.09555823 15.10042666 14.22664106 21.92460147 14.05918596
 25.04665714 24.03052362 15.64154406 13.677119

  8.45028161 12.10685658 16.2548474   9.43823117 15.66221638 13.52750279]
[23.46183808 25.12061299 16.59484941 14.15976038 22.16576113 16.86066247
 22.81594547 20.00173576 21.33715515 15.1700035  16.54217786 46.20899682
  8.6752005  12.04259106 16.35981156 10.41123635 17.23037364 14.70755924]
[20.65839621 25.66752839 17.03311974 13.95866665 21.85120678 18.65285092
 21.93243396 19.54592526 25.03326205 14.82463996 14.67399601 43.71663747
  8.54553069 12.06366538 16.24561784  9.53673092 14.94763415 16.00597656]
[21.34829721 26.12454882 17.03196102 14.03129331 22.19880915 15.25845646
 20.98075207 22.66488289 20.27497808 14.21084484 14.20194153 47.082234
  8.40276078 12.01237257 16.66845265  9.48935359 14.88073591 14.61537037]
[21.87655814 25.09903584 16.6095665  14.01162562 21.87665176 16.66114412
 21.74356413 19.37720597 21.47741892 15.44242808 15.44743442 45.73994683
  8.60130312 12.08329226 16.12527337 10.64532621 17.62277997 13.92646633]
[20.31426152 27.48508292 17.60721561 14.16403663

...

[19.45932851 23.10668322 15.36372321 16.11242789 25.4450416  11.52784024
 13.08497936 11.55730887 15.13253894 14.36861464 11.0924496  13.38235377
  6.69231136 11.42929241 13.11507936  7.88001375 10.48958365  8.69501605]
[19.49910412 23.25989118 15.35376902 16.1512563  25.55015648 11.46986095
 13.09299756 11.48633041 15.19210525 14.16879426 11.06731543 13.44329496
  6.6844968  11.4169697  13.08963512  7.83411107 10.35521386  8.70909095]
[19.38461886 23.15288009 15.32645737 16.0872788  25.4713208  11.48969873
 13.08937266 11.57262309 15.18867632 14.24690977 11.09345977 13.42493747
  6.6925229  11.41596237 13.10687684  7.82161748 10.40245537  8.72402974]
[19.41741632 23.20435592 15.34364121 16.11078323 25.48161302 11.54436152
 13.09097403 11.56423166 15.07320229 14.18668726 11.02508864 13.37292041
  6.67998801 11.45598537 13.08233401  7.83360489 10.37385232  8.72200076]
[19.59941603 23.31984164 15.39387436 16.16430807 25.57984304 11.50541953
 13.23783391 11.64672512 15.17661937 14.2332808

[19.63750785 22.98842411 15.40719112 15.8865565  24.51755498 11.58340904
 13.00140227 11.83779265 15.07113624 14.38995949 11.02368166 13.59099067
  6.708402   11.43973883 13.06183791  7.71688544 10.5643301   8.84500753]
[19.82375239 22.98971418 15.42735907 15.8665633  24.42608942 11.71514153
 13.05960372 11.90484096 15.13911443 14.49581992 11.08319666 13.76437228
  6.72745329 11.45971444 13.15673448  7.71224594 10.67782091  8.8512499 ]
[19.42856585 22.88160813 15.36690514 15.81220562 24.50167012 11.52907393
 12.82328445 11.65423845 14.93123774 14.31615436 10.89987331 13.44945099
  6.69240392 11.41708661 13.04399239  7.68129519 10.39453138  8.92801325]
[19.57426394 23.06106281 15.44174989 15.92711051 24.40598362 11.40517024
 12.86875225 11.76125329 14.92454246 14.01319885 10.89134283 13.43670851
  6.66538997 11.43299364 12.89565071  7.5956001  10.36312284  8.7840948 ]
[19.4947767  23.05756478 15.46474842 15.98690988 24.74269905 11.40920208
 12.98164394 11.61697617 15.08381396 14.2387633

[20.72395661 24.16410872 15.6652143  15.85127848 22.46053314 11.53228666
 13.35813944 11.18119063 15.44060079 14.56071449 11.05678985 14.67310769
  6.76445777 11.19245695 12.81063819  7.88461762 10.35285986  9.14729539]
[21.04551185 24.36458316 15.70687909 15.89339935 22.43361656 11.7375417
 13.59919965 11.374916   15.43205368 14.29649627 11.00347196 14.6236272
  6.75311516 11.27225916 12.81108559  7.88446675 10.30870342  8.95448089]
[20.51142016 24.00802486 15.63538106 15.81414961 22.17127219 11.59710273
 13.35551944 11.44748554 15.11700893 14.30346616 10.90070502 14.21453166
  6.7273755  11.2816711  12.54231046  7.85461442 10.42279448  9.05710199]
[20.46819088 24.01078924 15.65138164 15.7972955  21.95768428 11.57143137
 13.43206451 11.62560952 15.07945432 14.31476986 10.87584162 14.04171954
  6.72202677 11.2980443  12.46642422  7.8973398  10.49105878  9.05361102]
[20.45956259 24.47528566 15.51391419 15.88883505 22.25223077 11.72803097
 13.25086404 11.17982707 15.31959092 14.6621665  

  6.5032513  11.20094925 13.56922215  7.7700922  10.02555612  8.28952205]
[17.50512031 26.56876288 15.76966074 14.68771487 18.0336574  10.91835161
 12.17625358 10.85945242 15.479712   13.27608641 10.19180916 13.93407006
  6.49021087 11.17336567 13.831902    7.81960152  9.97385918  8.23955992]
[18.56497528 26.74447302 15.79482476 15.09532983 18.3650222  11.10997807
 12.38035247 11.14198665 15.49472333 14.05386717 10.31977039 14.54417037
  6.56665703 11.23033825 13.2872606   7.77310912 10.30777232  8.50818492]
[18.25790959 27.0231279  15.88879037 15.16779454 18.47306344 11.07985347
 12.28194615 11.03460208 15.39985083 13.98706567 10.21720495 14.24446679
  6.51585778 11.286913   13.49694449  7.79619258 10.1793429   8.5067537 ]
[18.55213613 27.49158469 16.0264096  15.36211605 18.50050951 11.09970398
 12.19027855 11.04796358 15.53472324 14.25086872 10.2825808  14.37787361
  6.51137718 11.34213279 13.67023521  7.86305735 10.25841466  8.65746405]
[17.85051793 27.18482238 15.85174486 15.169907

Teams     Ranks  Draft Advantage 2
1           Team Liquid  2.783704           3.540573
4           Vici Gaming  1.789176           3.540573
0                    OG  1.767033           3.540573
8                Newbee  1.591374           3.540573
2               PSG.LGD  1.586739           3.540573
3           Team Secret  1.548051           3.540573
11               Fnatic  1.438666           3.540573
14        Natus Vincere  1.431800           3.540573
9          TNC Predator  1.428801           3.540573
6   Royal Never Give Up  1.352719           3.540573
5         Evil Geniuses  1.282752           3.540573
13              Mineski  1.280869           3.540573
7       Infamous Gaming  1.258248           3.540573
16          KEEN GAMING  1.237095           3.540573
10           Virtus.pro  1.222059           3.540573
17    Ninjas in Pyjamas  1.112360           3.540573
15   Chaos Esports Club  1.073208           3.540573
12             Alliance  1.012406           3.540573

In [41]:
Teamhg3

Teams     Ranks  Draft Advantage 2
1           Team Liquid  2.783704           3.540573
4           Vici Gaming  1.789176           3.540573
0                    OG  1.767033           3.540573
8                Newbee  1.591374           3.540573
2               PSG.LGD  1.586739           3.540573
3           Team Secret  1.548051           3.540573
11               Fnatic  1.438666           3.540573
14        Natus Vincere  1.431800           3.540573
9          TNC Predator  1.428801           3.540573
6   Royal Never Give Up  1.352719           3.540573
5         Evil Geniuses  1.282752           3.540573
13              Mineski  1.280869           3.540573
7       Infamous Gaming  1.258248           3.540573
16          KEEN GAMING  1.237095           3.540573
10           Virtus.pro  1.222059           3.540573
17    Ninjas in Pyjamas  1.112360           3.540573
15   Chaos Esports Club  1.073208           3.540573
12             Alliance  1.012406           3.540573

In [42]:
Teamhg3

Teams     Ranks  Draft Advantage 2
1           Team Liquid  2.783704           3.540573
4           Vici Gaming  1.789176           3.540573
0                    OG  1.767033           3.540573
8                Newbee  1.591374           3.540573
2               PSG.LGD  1.586739           3.540573
3           Team Secret  1.548051           3.540573
11               Fnatic  1.438666           3.540573
14        Natus Vincere  1.431800           3.540573
9          TNC Predator  1.428801           3.540573
6   Royal Never Give Up  1.352719           3.540573
5         Evil Geniuses  1.282752           3.540573
13              Mineski  1.280869           3.540573
7       Infamous Gaming  1.258248           3.540573
16          KEEN GAMING  1.237095           3.540573
10           Virtus.pro  1.222059           3.540573
17    Ninjas in Pyjamas  1.112360           3.540573
15   Chaos Esports Club  1.073208           3.540573
12             Alliance  1.012406           3.540573

In [43]:
import random
Train = random.sample(range(193), 97)
Train
total = range(193)
Test = []
for i in total:
    if i not in Train:
        Test.append(i)
Test

trainRadiant = games["Radiant"][97:]
trainDire = games["Dire"][97:]
trainWinner = games["Winner"][97:]

trainGames = pd.DataFrame(data = {'Radiant':trainRadiant,'Dire':trainDire,'Winner':trainWinner})
trainGames

testRadiant = games["Radiant"][0:96]
testDire = games["Dire"][0:96]
testWinner = games["Winner"][0:96]

testGames = pd.DataFrame(data = {'Radiant':testRadiant,'Dire':testDire,'Winner':testWinner})
testGames

Radiant                Dire  Winner
0             OG         Team Liquid     1.0
1    Team Liquid                  OG     0.0
2    Team Liquid                  OG     0.0
3    Team Liquid                  OG     1.0
4        PSG.LGD         Team Liquid     0.0
..           ...                 ...     ...
91   KEEN GAMING              Newbee     1.0
92       Mineski         Team Secret     1.0
93   Team Liquid            Alliance     1.0
94  TNC Predator  Chaos Esports Club     1.0
95   Team Secret             Mineski     1.0

[96 rows x 3 columns]

In [44]:
trainTeamsX = designMatrix(trainGames, index_dict)
trainTeams = BTfit(trainTeamsX, trainGames["Winner"], Teamlist,1)

In [45]:
trainTeams

Teams                   Ranks
0                    OG     [2.840385798173282]
1           Team Liquid   [-0.3046810887345014]
2               PSG.LGD    [1.9901626442372549]
3           Team Secret     [2.892053260280484]
4           Vici Gaming    [1.2795604021292535]
5         Evil Geniuses    [1.0521698545560705]
6   Royal Never Give Up    [-0.975257687074863]
7       Infamous Gaming    [1.3314696739609841]
8                Newbee    [1.2861607827156005]
9          TNC Predator    [1.1424430752350416]
10           Virtus.pro   [-0.9771617297025272]
11               Fnatic    [0.7043566292250386]
12             Alliance    [0.7448658902417994]
13              Mineski    [0.2033268315603538]
14        Natus Vincere    [1.0352982060976934]
15   Chaos Esports Club    [-1.879336589675658]
16          KEEN GAMING  [-0.05767535237306112]
17    Ninjas in Pyjamas    [-2.259397093942969]

In [46]:
wins = 0
for i in range(len(testGames["Radiant"])):
    li = trainTeams["Ranks"][index_dict[testGames["Radiant"][i]]][0]
    lj = trainTeams["Ranks"][index_dict[testGames["Dire"][i]]][0]
    result = testGames["Winner"][i]
    pi = li/(li + lj)
    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy1 = wins/len(testGames["Radiant"])
test_accuracy1

49


0.5104166666666666

In [47]:
heroes1 = []
heroes2 = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        heroes1.append(Stats[i][2])
        heroes2.append(Stats[i][5])
        i += 1   
heroes1new = []
heroes2new = []
for i in heroes1:
    heroes1new.append(i.split("  "))

for i in heroes2:
    heroes2new.append(i.split("  "))

    
trainHeroes1 = heroes1new[97:]
trainHeroes2 = heroes2new[97:]
testHeroes1 = heroes1new[0:96]
testHeroes2 = heroes2new[0:96]

Matchups1 = []
binWins2 = []
for i in trainHeroes1:
    for j in i:
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)


Matchups2 = []
for i in trainHeroes2:
    for j in range(5):
        Matchups2.append(i[0])
        Matchups2.append(i[1])
        Matchups2.append(i[2])
        Matchups2.append(i[3])
        Matchups2.append(i[4])

    
for i in binWins[97:]:
    for j in range(25):
        binWins2.append(i)

d = {'Radiant':Matchups1, 'Dire':Matchups2, 'Winner':binWins2}
trainHeroGames = pd.DataFrame(data = d)


In [48]:
trainHeroes1X = designMatrix(trainHeroGames, hdict)
trainHeroesSkill1 = BTfit(trainHeroes1X, binWins2, heroes,1)
trainHeroesSkill1

Teams                   Ranks
0                Io    [1.5893340803550933]
1              Tiny    [0.8923347864307171]
2           Abaddon    [0.7914379178579968]
3         Timbersaw  [0.004149155693118622]
4        Gyrocopter    [1.3475426607028447]
..              ...                     ...
110  Spirit Breaker   [-0.9442492647232976]
111   Night Stalker   [0.45399487590946896]
112   Bounty Hunter   [0.41117813217253885]
113      Venomancer    [-1.720781771765306]
114    Ember Spirit   [-0.9306950065924455]

[115 rows x 2 columns]

In [49]:
testTeamskill1 = np.zeros(96)
testTeamskill2 = np.zeros(96)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
testTeamskill1
testTeamskill2

array([ 7.50259507,  3.70739975,  4.48896446,  4.77678582,  6.20031762,
        2.58992321,  5.0605789 ,  4.90023232,  3.69133377,  4.89764381,
        2.86442133,  4.4137556 ,  4.99799713,  5.44349873,  4.84601914,
        5.49829519,  3.84934865,  5.21831539,  4.00776801,  5.26953966,
        4.63358376,  5.07591498,  7.12645345,  5.10212135,  3.92713596,
        2.58734916,  4.74711724,  2.19404583,  5.96307151,  3.90695605,
        6.57073392,  4.81468563,  5.24624681,  4.87174387,  4.63460062,
        5.60926128,  4.83655621,  6.23767846,  7.09666472,  4.69566201,
        4.20979374,  7.03325309,  3.67504091,  5.7823187 ,  5.51268422,
        5.5651508 ,  4.65577811,  6.33620983,  4.9823792 ,  3.93941145,
        4.24558141,  6.69749662,  3.44045285,  5.03213711,  5.19486685,
        5.10170913,  2.9431028 ,  5.00415241,  2.64353904,  2.70474954,
        2.42812053,  5.37805911,  6.67866348,  3.57942337,  5.3583989 ,
        4.90752767,  2.33219614,  4.522563  ,  3.18065437,  5.47

In [50]:
testTeamwin1 = 0
for i in range(96):
    prob = testTeamskill1[i]/(testTeamskill1[i]+testTeamskill2[i])
    result = testGames["Winner"][i]
    if prob < 0.5 and result ==0:
        testTeamwin1 += 1
    if prob >= 0.5 and result ==1:
        testTeamwin1 += 1
test_accuracy2 = testTeamwin1/len(testGames["Radiant"])
test_accuracy2


0.5

In [51]:
k = len(hdict.keys())
r = []

r = np.array(trainWinner)
m = len(r)



Ip = np.zeros((m,k))
I = np.zeros((m,k))
l = 0
for i in trainHeroes1:
    for j in i:
        if trainGames["Winner"][97+l] == 1:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l+=1

l = 0
for i in trainHeroes2:
    for j in i:
        if trainGames["Winner"][97+l] == 0:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l += 1  


trainHeroesSkill2 = BTfit2(I,Ip,r,k,10,heroes)

[2.79273355e-01 6.44402312e-02 1.98623614e-01 9.31682745e-01
 8.54413568e-01 9.54734735e-01 5.22533482e-02 5.79471681e-01
 4.80496267e-01 2.17089790e-02 3.73620464e-01 4.14091801e-01
 6.03907234e-01 6.71748727e-01 8.38865700e-01 7.79526208e-01
 4.00701044e-01 7.94529231e-01 8.93124310e-01 2.62489691e-01
 9.89197007e-01 8.53307099e-01 7.31477156e-01 3.55565625e-01
 8.83289491e-01 8.67959091e-01 9.55766446e-01 1.07256520e-04
 1.65410419e-02 3.14070057e-01 9.95316175e-01 1.48844223e-01
 1.67377119e-01 7.58572037e-01 6.95296662e-02 7.05473439e-01
 4.69165282e-01 1.01882161e-02 7.74823863e-01 7.94201008e-01
 1.49569452e-01 2.37036318e-02 7.62063771e-01 2.23670180e-01
 2.62174398e-01 4.56869503e-01 2.49926919e-01 5.68283562e-01
 8.46942997e-01 3.78099537e-01 4.32465116e-01 8.32619176e-01
 3.71131936e-01 4.05532719e-02 5.54671486e-01 4.51246243e-01
 7.25300977e-01 3.78450522e-01 8.40662496e-01 4.69314694e-01
 5.62643429e-01 6.61199339e-01 4.62241868e-01 6.23636945e-01
 2.21880631e-01 7.328631

c:\users\rowan\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:62: RuntimeWarning: invalid value encountered in double_scalars


In [52]:
testTeamskill3 = np.zeros(96)
testTeamskill4 = np.zeros(96)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
testTeamskill3
testTeamskill4

testTeamwin2 = 0
for i in range(96):
    prob = testTeamskill3[i]/(testTeamskill3[i]+testTeamskill4[i])
    result = testGames["Winner"][i]
    if prob < 0.5 and result ==0:
        testTeamwin2 += 1
    if prob >= 0.5 and result ==1:
        testTeamwin2 += 1
test_accuracy3 = testTeamwin2/len(testGames["Radiant"])
test_accuracy3

0.5520833333333334

In [53]:
wincounts = np.zeros(len(Teamlist))
index = 97
for i in trainGames["Radiant"]:
    if trainGames["Winner"][index] == 1:
        wincounts[index_dict[i]] += 1
    index+=1

index = 97
for i in trainGames["Dire"]:
    if trainGames["Winner"][index] == 0:
        wincounts[index_dict[i]] += 1
    index+=1
    
wincounts

array([11.,  3., 10.,  9.,  7.,  6.,  3.,  5.,  5.,  6.,  3.,  5.,  5.,
        5.,  7.,  1.,  4.,  1.])

In [73]:
trainTeamskill1 = np.zeros(m)
trainTeamskill2 = np.zeros(m)

index = 0
for i in trainHeroes1:
    for j in i:
        trainTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in trainHeroes2:
    for j in i:
        trainTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1

trainTeamskill3 = np.zeros(m)
trainTeamskill4 = np.zeros(m)

index = 0
l = 97
for i in trainHeroes1:
    for j in i:
        if trainGames["Winner"][l] == 1:
            trainTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
        trainTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    l += 1
    
index = 0
l = 97
for i in trainHeroes2:
    for j in i:
        if trainGames["Winner"][l] == 0:
            trainTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
        trainTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    l += 1
    
trainTeamwin1 = np.zeros(m)
for i in range(m):
    prob = trainTeamskill1[i]/(trainTeamskill1[i] + trainTeamskill2[i])
    if prob >= 0.5:
        trainTeamwin1[i] = 1    

trainTeamwin2 = np.zeros(m)
for i in range(m):
    if (trainTeamskill3[i]/trainTeamskill4[i]) > 0.5:
        trainTeamwin2[i] = 1

trainGames["Team Winner"] =trainTeamwin1
trainGames["Team Winner 2"] = trainTeamwin2

k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 97

for i in trainGames["Radiant"]:
    j = trainGames["Dire"][l]
    if trainGames["Team Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(trainGames["Team Winner"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 1":np.exp(res.x[-1])}


Teamhg3 = pd.DataFrame(data)


k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 97
for i in trainGames["Radiant"]:
    j = trainGames["Dire"][l]
    if trainGames["Team Winner 2"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(trainGames["Team Winner 2"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')
data = {"Teams":Teamlist, "Ranks":res.x[:-1]/np.min(res.x[:-1]),"Draft Advantage 2":res.x[-1]}

Teamhg4 = pd.DataFrame(data)


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

[27.43023478 17.79500642 15.33575899 15.45877386 22.65803403 11.86012245
 12.15248091 17.81397366 16.12788071 13.71082469 13.40864072 25.66698676
  8.57948427 10.53227251 16.22732256 14.86124521 23.05121857 16.65156841]
[26.8020074  17.3691805  14.97437775 15.29231577 22.24273507 11.97248541
 14.96059847 17.98540532 16.34494288 15.6255673  14.9334087  26.83038501
  8.83791855 10.82213625 16.19199481 15.5645793  23.23995114 18.58686651]
[25.10230768 16.57768526 14.43378355 14.69600496 20.71494218 11.38065139
 12.28006532 16.89755912 15.06921119 13.93531329 13.67741503 24.53185312
  8.70511319 10.52214957 15.42534108 14.32127822 21.83032726 16.79500051]
[27.19270958 17.27801301 15.40369895 15.49013532 22.35202917 11.16972297
 14.59010607 17.78396146 15.37452559 14.61729621 13.49478746 26.70735906
  8.66384291 10.84868181 16.32651457 15.19374571 24.21389938 18.08767524]
[26.16689493 16.79658951 14.61751444 14.89048869 21.97370875 13.00955143
 13.33858222 17.71418562 14.65599739 15.1054129

c:\users\rowan\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log


[15.16856316 17.90547064 13.15031666 15.0088058  13.86898228 11.85505548
 10.86174858 15.55743934 13.27032219 12.32144053 11.20839457 18.3817507
  7.54036725  8.86028081 15.5394372   8.10906781 13.44367964  8.85397193]
[15.0558549  17.37450234 12.86583821 14.65349816 13.45452765 11.49411557
 10.19128445 15.25437427 12.84528024 12.17603013 11.09956085 18.05222123
  7.52824022  8.81777814 15.14267161  8.01042934 13.21571797  8.88996032]
[13.89578087 16.77784711 12.35010897 14.18322214 12.4778316  11.07102098
  9.86888179 14.52576723 12.40797456 12.06751766 11.02514911 17.33165526
  7.47771512  8.67890042 14.66522507  7.9168636  12.26505531  8.83775381]
[15.36584789 17.80309973 13.21261068 14.88835473 13.60260385 11.15387229
 10.22791227 15.32031516 12.62622425 11.56223181 10.51459538 18.38790631
  7.42875319  8.89830002 15.3930137   7.92013064 13.79719607  8.83037135]
[14.55941359 17.68348667 13.06007294 14.69569662 12.8182412  10.46176722
  9.96425176 14.7240386  12.04113072 10.94183259

[13.63513111 16.33477881 13.00312048 14.00571311 13.25284533 11.65275716
  9.2384927   9.6691681  12.47221892 13.46010522  9.01277207 15.10974406
  7.03784735  8.39590393 16.13772663  7.49587767 10.81781459  8.06274077]
[16.14149566 17.24063668 13.65808811 14.5668338  12.99326066 11.22802668
  9.6934718  10.27083138 13.69909408 13.09290724  8.3468419  16.71275085
  7.064605    8.68072765 16.83451601  7.71949144 11.42155332  8.2093446 ]
[14.404787   16.10624597 12.83589162 13.76809824 13.44696093 11.38804331
  8.83786126  9.60381486 11.94626203 13.06179977  8.84213515 15.29088395
  7.05703769  8.47154562 15.76393077  7.48112915 10.85689832  8.18876803]
[14.69007064 16.57853109 13.37048041 14.21781232 14.2499938  11.56772345
  8.73020915  9.93722022 12.62445818 13.61360677  8.95894456 15.77979251
  7.08073622  8.62964271 16.43126227  7.74547948 11.9451717   8.68893698]
[13.91657277 16.32241299 12.82973654 13.71652021 12.87627352 10.88958159
  8.75341687  8.78255825 11.17473933 12.3922899

...

  6.05803811 14.54635083 12.38524276  5.89582321  7.91667114  6.4828634 ]
[15.70151193 11.93639856 10.96262401 15.6065851  16.53310308 10.75516424
  7.94871074 11.1345484  11.53026485 11.07612908  8.25673626 13.84193162
  6.02968729 14.87228045 12.40839743  6.03514517  8.14583136  6.24766646]
[15.29708915 11.868418   11.10416692 15.66485672 16.66458253 10.57020424
  8.0756964  10.98506659 11.76561607 10.92970142  7.97194831 14.23329062
  6.02307328 14.67987219 12.30116242  6.1304957   7.89216349  6.27851919]
[15.90526055 12.03011027 11.10887383 15.72990201 16.84086691 10.88091321
  7.74766492 11.20356031 11.59676115 11.27030096  8.46881632 13.99249575
  6.04538959 14.80889513 12.4445048   5.93104729  8.15268449  6.34031593]
[15.47660075 11.9218017  11.20760407 15.50950695 16.64841258 10.62706177
  7.78167922 11.25363294 11.68014882 11.57108273  8.29664723 15.00017392
  6.08294501 14.53472104 12.04915428  6.12114966  8.12567881  6.46421422]
[15.81330546 12.00327186 11.06359561 15.796170

[15.52091719 11.75737797 10.93458712 15.74390875 16.7520887  10.53379206
  7.84214814 10.96298444 11.46470539 11.76380261  7.96676269 13.96133025
  5.99906863 15.02485053 12.56305269  5.85845012  7.9758766   6.3071404 ]
[15.31335711 11.6947474  10.8798994  15.66484278 16.62984072 10.36994825
  7.82507773 10.91547467 11.39356216 11.68446247  7.93730341 13.70052494
  5.97987107 14.9941022  12.53459147  5.84361752  7.90212703  6.29585432]
[15.42170655 11.76098863 10.92987191 15.76090005 16.83152489 10.48675131
  7.81040951 10.99101908 11.49208235 11.78127359  7.93044998 13.8440576
  5.99342648 15.01729431 12.59596771  5.83696389  7.99094784  6.31126286]
[15.49737882 11.71607355 10.91205808 15.69966235 16.62091874 10.48113933
  7.83224795 10.9033987  11.45898252 11.7400808   7.95603324 13.78366555
  5.99167879 14.96898974 12.47993753  5.84785655  7.92790843  6.32552488]
[15.51242305 11.68847933 10.9219693  15.70512934 16.57044624 10.51658094
  7.83048945 10.85660489 11.42799279 11.78110027

[15.43008092 11.39263467 11.29021479 17.02648359 16.50177817 10.37669131
  7.86896411 11.27545128 10.8213637  11.59632539  7.90754317 13.84352263
  5.89859525 14.50504194 11.69902296  5.77382119  8.06074465  6.23396205]
[15.40627367 11.4409696  11.31311761 17.16331788 16.77093463 10.24441742
  7.93213408 11.23841174 11.14386087 11.4007284   7.71066381 13.76722721
  5.89030597 14.57256315 11.85612114  5.7210341   8.00201244  6.22148651]
[15.19265265 11.32069796 11.14323569 16.84941396 16.21396507 10.10236303
  7.86602077 11.10976092 10.85771525 11.29920861  7.70960755 13.46967619
  5.86727616 14.56861829 11.65505577  5.7811556   7.92391778  6.2043851 ]
[15.44192666 11.42831121 11.19697953 16.97727021 16.66364889 10.05956795
  7.92839058 11.26120213 11.06624943 11.51859265  7.82052707 13.34509868
  5.88653152 14.66159078 11.92358137  5.71023397  8.00750955  6.19971899]
[15.3116403  11.35856668 11.28054925 17.13603161 16.55640593 10.08977477
  7.88520999 11.21417555 10.9025239  11.3296969

  5.87964185 14.95681881 12.10847888  5.73112202  7.99904181  6.17091424]
[16.12264067 11.32839254 11.1444499  17.48951242 16.63407504  9.87873167
  7.93096844 11.20278658 10.85250703 11.41312511  7.86981635 13.87441804
  5.87347507 15.00292904 12.11863525  5.6890271   8.01611233  6.25464808]
[15.86486735 11.29615423 11.10191915 17.32612609 16.45468102  9.90716455
  7.93161091 11.10445997 10.81483543 11.28221473  7.79515247 13.75241344
  5.863383   14.95406495 12.05446589  5.71311644  7.95144973  6.27251548]
[15.90422835 11.29141642 11.13936614 17.43092233 16.49329101  9.83382251
  7.8838143  11.18073187 10.76343261 11.29656919  7.83506463 13.79889268
  5.85887601 14.92091241 11.98873704  5.71144621  7.96457552  6.21007878]
[16.07934597 11.38422381 11.13093642 17.35912827 16.70582947  9.78464416
  7.92063695 11.23703578 10.99366099 11.40306191  7.87488852 13.88505523
  5.8857261  15.01110242 12.16384589  5.71459299  8.0205918   6.24890795]
[15.98083467 11.27106634 11.10193648 17.387288

  5.87327193 14.20224793 12.30676896  5.75285172  8.0584036   6.18095595]
[16.59078016 10.99931956 11.05911981 18.0843601  16.82605409  9.76848146
  7.92961422 11.03553996 10.79808235 11.65728431  7.88889158 14.04552132
  5.89991333 14.44317616 12.40037806  5.7473296   8.05295504  6.2111475 ]
[16.04240516 11.02322095 11.07951888 17.77197674 16.62141004  9.88325688
  7.96184582 11.01019967 10.74900882 11.46199388  7.84757577 13.85214068
  5.88911915 14.34140231 12.21896713  5.80115549  7.99786761  6.2692992 ]
[16.29657326 10.87532508 11.04101235 18.13038464 16.69828081  9.84225261
  7.93655414 10.96002313 10.58835178 11.60319907  7.83138674 13.99976113
  5.88534948 14.25622482 12.33668589  5.81235845  8.0190871   6.20304392]
[16.47068562 11.01254888 11.09381683 18.12180278 17.09519614  9.9427102
  8.04586406 11.08888603 10.79750017 11.71438003  7.98705066 14.03854442
  5.91856917 14.31693611 12.63771114  5.76682015  8.11639277  6.2368599 ]
[16.11906309 10.9941823  11.08344195 17.8358300

In [74]:
Teamhg4

Teams      Ranks  Draft Advantage 2
0                    OG  16.105615            1.26173
1           Team Liquid   8.212330            1.26173
2               PSG.LGD   8.453914            1.26173
3           Team Secret  18.947449            1.26173
4           Vici Gaming  16.885495            1.26173
5         Evil Geniuses   6.914868            1.26173
6   Royal Never Give Up   4.125893            1.26173
7       Infamous Gaming   8.459233            1.26173
8                Newbee   8.099027            1.26173
9          TNC Predator   9.355769            1.26173
10           Virtus.pro   4.007160            1.26173
11               Fnatic  12.720087            1.26173
12             Alliance   1.138338            1.26173
13              Mineski  12.688821            1.26173
14        Natus Vincere  10.819861            1.26173
15   Chaos Esports Club   1.000000            1.26173
16          KEEN GAMING   4.421653            1.26173
17    Ninjas in Pyjamas   1.698976            1.26173

In [56]:
testTeamskill1 = np.zeros(m)
testTeamskill2 = np.zeros(m)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1

testTeamskill3 = np.zeros(m)
testTeamskill4 = np.zeros(m)

index = 0
for i in testHeroes1:
    for j in i:
        if testGames["Winner"][index] == 1:
            testTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        if testGames["Winner"][index]==0:
            testTeamskill3[index]+= trainHeroesSkill2["Ranks"][hdict[j]]
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    
testTeamwin1 = np.zeros(m)
for i in range(m):
    prob = testTeamskill1[i]/(testTeamskill1[i]+testTeamskill2[i])
    if prob >= 0.5:
        testTeamwin1[i] = 1    

testTeamwin2 = np.zeros(m)
for i in range(m):
    if testTeamskill3[i]/(testTeamskill4[i]) > 0.5:
        testTeamwin2[i] = testGames["Winner"][i]

testGames["Team Winner"] = testTeamwin1
testGames["Team Winner 2"] = testTeamwin2


wins = 0
for i in range(len(testGames["Radiant"])-1):
    li = Teamhg3["Ranks"][index_dict[testGames["Radiant"][i]]]
    lj = Teamhg3["Ranks"][index_dict[testGames["Dire"][i]]]
    result = testGames["Winner"][i]
    if testGames["Team Winner"][i]== 1:
        """Radiant is home team"""
        pi = Teamhg3["Draft Advantage 1"][0]*li/(Teamhg3["Draft Advantage 1"][0]*li + lj)
    elif 0 == testGames["Team Winner"][i]:
        """Dire is home team"""
        pi = li/(Teamhg3["Draft Advantage 1"][0]*lj + li)        

    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy4 = wins/len(testGames["Radiant"])
test_accuracy4

47


0.4895833333333333

In [57]:
wins = 0
for i in range(len(testGames["Radiant"])-1):
    li = Teamhg4["Ranks"][index_dict[testGames["Radiant"][i]]]
    lj = Teamhg4["Ranks"][index_dict[testGames["Dire"][i]]]
    result = testGames["Winner"][i]
    if testGames["Team Winner 2"][i]== 1:
        """Radiant is winning team"""
        pi = Teamhg4["Draft Advantage 2"][0]*li/(Teamhg4["Draft Advantage 2"][0]*li + lj)
    elif 0 == testGames["Team Winner 2"][i]:
        """Dire is winning team"""
        pi = li/(Teamhg4["Draft Advantage 2"][0]*lj + li)        

    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy5 = wins/len(testGames["Radiant"])
test_accuracy5

58


0.6041666666666666

In [58]:
test2.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [59]:
testTeamwin2

array([0., 0., 0., 1., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 1.,
       0., 1., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 1., 1., 0.,
       0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 1., 0.,
       1., 0., 0., 0., 0., 0., 1., 0., 1., 0., 0., 1., 0., 0., 0., 1., 1.,
       0., 0., 1., 1., 0., 1., 0., 1., 1., 0., 1.])

In [60]:
test_accuracy1

0.5104166666666666

In [61]:
test4.sort_values(by=['Ranks'], inplace=True, ascending=False)

#### 

In [62]:
test4[:18]

Teams                 Ranks
75      Winter Wyvern  [2.9125007334122492]
18          Dark Seer   [2.147074236489597]
21             Tinker  [2.0473852065186655]
37         Windranger   [2.026770413536992]
0                  Io  [1.9963013796061508]
102  Treant Protector  [1.9939669002202651]
13               Chen   [1.756651040412916]
14              Meepo  [1.6565872624962308]
111     Night Stalker  [1.6235947315356913]
78        Monkey King   [1.602031121802458]
8    Templar Assassin  [1.5878814862799928]
97            Slardar   [1.529911393917902]
2             Abaddon  [1.4212891456657923]
16      Faceless Void  [1.3819261247874097]
40             Medusa  [1.3682957813704135]
86      Skywrath Mage  [1.3468661580904757]
6          Tidehunter  [1.3409873276619968]
4          Gyrocopter  [1.2940120134221111]

In [63]:
Teamhg4

Teams     Ranks  Draft Advantage 2
0                    OG  0.537519            1.26173
1           Team Liquid  0.274083            1.26173
2               PSG.LGD  0.282146            1.26173
3           Team Secret  0.632364            1.26173
4           Vici Gaming  0.563547            1.26173
5         Evil Geniuses  0.230781            1.26173
6   Royal Never Give Up  0.137700            1.26173
7       Infamous Gaming  0.282324            1.26173
8                Newbee  0.270302            1.26173
9          TNC Predator  0.312245            1.26173
10           Virtus.pro  0.133738            1.26173
11               Fnatic  0.424528            1.26173
12             Alliance  0.037992            1.26173
13              Mineski  0.423485            1.26173
14        Natus Vincere  0.361109            1.26173
15   Chaos Esports Club  0.033375            1.26173
16          KEEN GAMING  0.147571            1.26173
17    Ninjas in Pyjamas  0.056703            1.26173

In [64]:
test5.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [65]:
test5[:18]

Heroes     Ranks
41        Ember Spirit  0.023769
51         Earthshaker  0.023092
69          Grimstroke  0.021431
1                 Tiny  0.020281
43            Silencer  0.019167
5               Rubick  0.018819
48   Centaur Warrunner  0.018440
58              Kunkka  0.018382
2              Abaddon  0.017755
100         Lone Druid  0.017607
91               Pudge  0.016662
28           Alchemist  0.016517
52              Oracle  0.016416
13                Chen  0.016252
17        Shadow Fiend  0.016161
19                Sven  0.016012
65               Slark  0.015083
68         Beastmaster  0.015054

In [66]:
test_accuracy3

0.5520833333333334

In [67]:
Teamhg

Teams      Ranks  Radiant Advantage
0                    OG  18.053787           0.915161
1           Team Liquid  15.822115           0.915161
14        Natus Vincere  15.641570           0.915161
3           Team Secret  13.610140           0.915161
4           Vici Gaming  13.523732           0.915161
2               PSG.LGD  11.035274           0.915161
13              Mineski  10.865921           0.915161
8                Newbee  10.634655           0.915161
6   Royal Never Give Up   9.441427           0.915161
5         Evil Geniuses   8.551742           0.915161
9          TNC Predator   8.062199           0.915161
11               Fnatic   7.491167           0.915161
7       Infamous Gaming   6.233234           0.915161
16          KEEN GAMING   5.833543           0.915161
10           Virtus.pro   4.816592           0.915161
17    Ninjas in Pyjamas   3.058589           0.915161
15   Chaos Esports Club   2.348975           0.915161
12             Alliance   1.000000           0.915161

In [72]:
Teamhg3

Teams     Ranks  Draft Advantage 1
0                    OG  2.013910           2.142735
1           Team Liquid  1.343531           2.142735
2               PSG.LGD  1.569671           2.142735
3           Team Secret  1.868233           2.142735
4           Vici Gaming  1.592119           2.142735
5         Evil Geniuses  1.278382           2.142735
6   Royal Never Give Up  1.182304           2.142735
7       Infamous Gaming  1.305086           2.142735
8                Newbee  1.379038           2.142735
9          TNC Predator  1.433063           2.142735
10           Virtus.pro  1.187189           2.142735
11               Fnatic  1.303137           2.142735
12             Alliance  1.035370           2.142735
13              Mineski  1.202711           2.142735
14        Natus Vincere  2.176091           2.142735
15   Chaos Esports Club  1.047717           2.142735
16          KEEN GAMING  1.266254           2.142735
17    Ninjas in Pyjamas  1.109520           2.142735

In [69]:
test_accuracy4

0.4895833333333333

In [70]:
test_accuracy5

0.6041666666666666

In [71]:
teamhg3

NameError: name 'teamhg3' is not defined

In [ ]:
Teamhg3

In [ ]:
testGames

In [ ]:
testHeroes1

In [ ]:
Teamhg3

Need to do some testing against coin-flip

In [75]:
cointoss = []
for i in range(10000):
    wins = 0
    for i in testGames["Winner"]:
        if i == random.randint(0,1):
            wins+=1
    cointoss.append(wins)

In [76]:
np.mean(cointoss)/len(testGames["Winner"])

0.499771875

In [77]:
sum(binWins)/len(binWins)

0.46113989637305697

In [ ]:
teamhg

In [78]:
cointoss

[47,
 55,
 50,
 50,
 41,
 48,
 54,
 47,
 55,
 46,
 45,
 52,
 52,
 50,
 48,
 48,
 49,
 52,
 44,
 43,
 45,
 46,
 55,
 49,
 45,
 47,
 42,
 51,
 60,
 53,
 50,
 53,
 43,
 50,
 48,
 50,
 41,
 51,
 52,
 47,
 44,
 59,
 57,
 43,
 48,
 50,
 42,
 43,
 58,
 50,
 54,
 45,
 46,
 48,
 46,
 54,
 48,
 45,
 50,
 47,
 48,
 54,
 51,
 54,
 55,
 52,
 40,
 46,
 50,
 51,
 49,
 44,
 55,
 54,
 50,
 48,
 45,
 55,
 43,
 52,
 48,
 48,
 42,
 42,
 48,
 53,
 50,
 43,
 43,
 52,
 51,
 52,
 42,
 47,
 46,
 47,
 55,
 51,
 46,
 42,
 49,
 38,
 47,
 54,
 48,
 56,
 45,
 47,
 56,
 40,
 43,
 52,
 48,
 48,
 39,
 49,
 45,
 49,
 44,
 50,
 45,
 43,
 46,
 48,
 42,
 53,
 48,
 54,
 56,
 48,
 51,
 48,
 52,
 39,
 35,
 59,
 55,
 49,
 51,
 47,
 50,
 57,
 48,
 49,
 43,
 43,
 51,
 49,
 50,
 45,
 49,
 46,
 49,
 56,
 42,
 47,
 48,
 52,
 39,
 42,
 43,
 50,
 51,
 54,
 52,
 51,
 41,
 46,
 41,
 42,
 46,
 50,
 42,
 48,
 49,
 39,
 48,
 53,
 51,
 43,
 47,
 42,
 50,
 41,
 50,
 47,
 51,
 57,
 54,
 53,
 52,
 53,
 42,
 46,
 45,
 53,
 52,
 57,
 43,
 46,


In [79]:
test_accuracy1

0.5104166666666666

In [80]:
test_accuracy2

0.5

In [81]:
test_accuracy3

0.5520833333333334

In [82]:
test_accuracy4

0.4895833333333333

In [84]:
test_accuracy5

0.6041666666666666

In [85]:
np.mean(cointoss)/len(testGames["Winner"])

0.499771875